In [235]:
from dash import *
import dash_bootstrap_components as dbc

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import plotly.express as px #if using plotly
import geopandas as gpd
import os
import numpy as np
import pyproj

from plotly.graph_objects import Layout
import plotly.graph_objects as go



In [236]:
# # test files
# df_cases = pd.read_csv('phe_cases_london_boroughs.csv')
# df_deaths = pd.read_csv('phe_deaths_london_boroughs.csv')
# df_vaccination = pd.read_csv('phe_vaccines_age_london_boroughs.csv')


population = pd.read_csv('london_population_2020.csv')

#retrieving data directly from UK London Covid Data Website.
#https://data.london.gov.uk/dataset/coronavirus--covid-19--cases
df_cases = pd.read_csv('https://data.london.gov.uk/download/coronavirus--covid-19--cases/151e497c-a16e-414e-9e03-9e428f555ae9/phe_cases_london_boroughs.csv')
df_deaths = pd.read_csv('https://data.london.gov.uk/download/coronavirus--covid-19--cases/ff60cf44-852e-425e-960c-869920dcdd0d/phe_deaths_london_boroughs.csv')
df_vaccination = pd.read_csv('https://data.london.gov.uk/download/coronavirus--covid-19--cases/ae4d5fc9-5448-49a6-810f-910f7cbc9fd2/phe_vaccines_age_london_boroughs.csv')


In [237]:
df_cases_clean = df_cases.copy().drop(columns= ['area_code', 'total_cases'])
df_deaths_clean = df_deaths.copy().drop(columns= ['area_code', 'total_deaths'])
df_deaths_clean

area_name        date  new_deaths
0      Barking and Dagenham  2020-03-09           0
1                    Barnet  2020-03-09           0
2                    Bexley  2020-03-09           0
3                     Brent  2020-03-09           0
4                   Bromley  2020-03-09           0
...                     ...         ...         ...
24219                Sutton  2022-04-04           0
24220         Tower Hamlets  2022-04-04           0
24221        Waltham Forest  2022-04-04           0
24222            Wandsworth  2022-04-04           0
24223           Westminster  2022-04-04           0

[24224 rows x 3 columns]

In [238]:
df_merged = df_cases_clean.merge(df_deaths_clean, on=["area_name", "date"])
df_merged = df_merged.merge(population, on="area_name")
df_merged

area_name        date  new_cases  new_deaths     ONS  \
0      Barking and Dagenham  2020-03-09          1           0  214107   
1      Barking and Dagenham  2020-03-10          0           0  214107   
2      Barking and Dagenham  2020-03-11          1           0  214107   
3      Barking and Dagenham  2020-03-12          4           0  214107   
4      Barking and Dagenham  2020-03-13          1           0  214107   
...                     ...         ...        ...         ...     ...   
24187           Westminster  2022-03-30        188           0  269848   
24188           Westminster  2022-03-31        171           0  269848   
24189           Westminster  2022-04-01        149           0  269848   
24190           Westminster  2022-04-02         83           0  269848   
24191           Westminster  2022-04-03         52           0  269848   

          GLA  Difference  
0      214606         499  
1      214606         499  
2      214606         499  
3      214606         499  
4      214606         499  
...       ...         ...  
24187  265990       -3858  
24188  265990       -3858  
24189  265990       -3858  
24190  265990       -3858  
24191  265990       -3858  

[24192 rows x 7 columns]

In [267]:
# #get the latest date.
currentDate = df_merged['date'].iloc[-1]
previousDate = df_merged['date'].iloc[-2]

total_cases = df_merged['new_cases'].sum()
new_cases = df_merged.copy().loc[df_merged['date'] == currentDate]['new_cases'].sum()
new_cases

new_cases_previous = df_merged.copy().loc[df_merged['date'] == previousDate]['new_cases'].sum()

total_deaths = df_merged['new_deaths'].sum()
new_deaths = df_merged.copy().loc[df_merged['date'] == currentDate]['new_deaths'].sum()
new_deaths_previous = df_merged.copy().loc[df_merged['date'] == previousDate]['new_deaths'].sum()


#calculating daily case pattern in the past 14 days.
last14Days = df_merged.copy().groupby(['date']).sum().tail(14)
last14Days_graph = px.bar(last14Days, x=last14Days.index, y=last14Days['new_cases'], title="Daily Cases in the Last 14 Days")

In [268]:
#retrieve most recent vaccination rate data on 3rd dose.
df_3rdDose = df_vaccination.copy().loc[df_vaccination['dose'] == '3rd dose']
df_3rdDose = df_3rdDose.loc[df_3rdDose['date'] == currentDate]


df_3rdDose

area_name  area_code        date      dose       age_band  \
21675   Barking and Dagenham  E09000002  2022-04-03  3rd dose  12 - 15 years   
21676   Barking and Dagenham  E09000002  2022-04-03  3rd dose  16 - 17 years   
21677   Barking and Dagenham  E09000002  2022-04-03  3rd dose  18 - 24 years   
21678   Barking and Dagenham  E09000002  2022-04-03  3rd dose  25 - 29 years   
21679   Barking and Dagenham  E09000002  2022-04-03  3rd dose  30 - 34 years   
...                      ...        ...         ...       ...            ...   
694030           Westminster  E09000033  2022-04-03  3rd dose  60 - 64 years   
694031           Westminster  E09000033  2022-04-03  3rd dose  65 - 69 years   
694032           Westminster  E09000033  2022-04-03  3rd dose  70 - 74 years   
694033           Westminster  E09000033  2022-04-03  3rd dose  75 - 79 years   
694034           Westminster  E09000033  2022-04-03  3rd dose      80+ years   

        age_higher  age_lower  cum_doses  new_doses  population  new_prop  \
21675           15         12          2          0       13415  0.000000   
21676           17         16        301          2        5541  0.000361   
21677           24         18       3627          1       17719  0.000056   
21678           29         25       3599          3       15880  0.000189   
21679           34         30       5019          0       17683  0.000000   
...            ...        ...        ...        ...         ...       ...   
694030          64         60       7375          1       11815  0.000085   
694031          69         65       5733          0       10060  0.000000   
694032          74         70       5128          0        8575  0.000000   
694033          79         75       4012          1        6010  0.000166   
694034          90         80       5055          0        9255  0.000000   

        cum_prop  
21675   0.000149  
21676   0.054322  
21677   0.204696  
21678   0.226637  
21679   0.283832  
...          ...  
694030  0.624207  
694031  0.569881  
694032  0.598017  
694033  0.667554  
694034  0.546191  

[480 rows x 12 columns]

In [269]:
#calculating cases per 100,000 people. easier borough comparisons.
df_merged['cases_per_100k'] = round(df_merged['new_cases'] / df_merged['ONS'] * 100000)
df_merged['deaths_per_100k'] = round(df_merged['new_deaths'] / df_merged['ONS'] * 100000)
df_merged.head()


#shows line chart of past total covid cases in London
df1 = df_merged.copy().groupby(['date']).sum().drop(columns= ['GLA', 'ONS', 'cases_per_100k', 'deaths_per_100k', 'Difference'])
x = df1.index
y = df1['new_cases']

dailyCases = px.line(df1, x=x, y=y, title="Daily Covid19 Case in London")

##change in cases and deaths.
dailyCasesChange = df1['new_cases'].iloc[-1] - df1['new_cases'].iloc[-2]
dailyDeathsChange = df1['new_deaths'].iloc[-1] - df1['new_deaths'].iloc[-2]

In [270]:
#vaccination rate in London overall
vax_rate = round((df_3rdDose['cum_doses'].sum() / df_3rdDose['population'].sum())*100)
vax_rate

57

In [271]:
df_vaccinationYoung = df_3rdDose.loc[df_3rdDose['age_lower'] < 18]
df_vaccinationAdult = df_3rdDose.loc[df_3rdDose['age_lower'] < 65]
df_vaccinationOld = df_3rdDose.loc[df_3rdDose['age_lower'] >= 65]

In [272]:
df_vaccinationOld

area_name  area_code        date      dose       age_band  \
21686   Barking and Dagenham  E09000002  2022-04-03  3rd dose  65 - 69 years   
21687   Barking and Dagenham  E09000002  2022-04-03  3rd dose  70 - 74 years   
21688   Barking and Dagenham  E09000002  2022-04-03  3rd dose  75 - 79 years   
21689   Barking and Dagenham  E09000002  2022-04-03  3rd dose      80+ years   
43376                 Barnet  E09000003  2022-04-03  3rd dose  65 - 69 years   
...                      ...        ...         ...       ...            ...   
672344            Wandsworth  E09000032  2022-04-03  3rd dose      80+ years   
694031           Westminster  E09000033  2022-04-03  3rd dose  65 - 69 years   
694032           Westminster  E09000033  2022-04-03  3rd dose  70 - 74 years   
694033           Westminster  E09000033  2022-04-03  3rd dose  75 - 79 years   
694034           Westminster  E09000033  2022-04-03  3rd dose      80+ years   

        age_higher  age_lower  cum_doses  new_doses  population  new_prop  \
21686           69         65       4673          0        6062  0.000000   
21687           74         70       3829          2        4823  0.000415   
21688           79         75       2774          1        3399  0.000294   
21689           90         80       3893          0        5523  0.000000   
43376           69         65      13406          1       15723  0.000064   
...            ...        ...        ...        ...         ...       ...   
672344          90         80       6694          0        8620  0.000000   
694031          69         65       5733          0       10060  0.000000   
694032          74         70       5128          0        8575  0.000000   
694033          79         75       4012          1        6010  0.000166   
694034          90         80       5055          0        9255  0.000000   

        cum_prop  
21686   0.770868  
21687   0.793904  
21688   0.816122  
21689   0.704871  
43376   0.852636  
...          ...  
672344  0.776566  
694031  0.569881  
694032  0.598017  
694033  0.667554  
694034  0.546191  

[128 rows x 12 columns]

In [273]:
df_vaccinationYoung_pct = df_vaccinationYoung['cum_doses'].sum() / df_vaccinationYoung['population'].sum()
df_vaccinationYoung_pct

0.03802717586862899

In [274]:
df_vaccinationAdult_pct = df_vaccinationAdult['cum_doses'].sum() / df_vaccinationAdult['population'].sum()
df_vaccinationAdult_pct

0.5232139126438868

In [275]:
df_vaccinationOld_pct = df_vaccinationOld['cum_doses'].sum() / df_vaccinationOld['population'].sum()
df_vaccinationOld_pct

0.8114247946885301

In [276]:
d = {'age_group': ['Young (12 - 17)', 'Adult (18 - 64)', 'Old (65+)'],
        'Vaccination_Rate': [df_vaccinationYoung_pct, df_vaccinationAdult_pct, df_vaccinationOld_pct]
        }
df = pd.DataFrame(data=d)

In [277]:
# reading in the shapefile
fp = "London_Borough_Excluding_MHW.shp"
map_df = gpd.read_file(fp)
# map_df = map_df[['NAME', 'geometry']]
map_df.to_crs(pyproj.CRS.from_epsg(4326), inplace=True)
map_df = map_df.rename(columns={"NAME": "area_name"})
map_df = map_df.drop(columns = ['HECTARES', 'NONLD_AREA', 'ONS_INNER', 'SUB_2009', 'SUB_2006'])

#using the coordinates, we can label each region by its GSS_CODE on the map.
map_df['coords'] = map_df['geometry'].apply(lambda x: x.representative_point().coords[:])
map_df['coords'] = [coords[0] for coords in map_df['coords']]



df_merged1 = map_df.merge(df_merged.copy().loc[df_merged['date'] == currentDate], on="area_name")

df_merged1.index = df_merged1['area_name']


# #weekly covid cases mapped onto a geographic map.
geo_cases = px.choropleth(df_merged1,
                    geojson=df_merged1.geometry,
                    locations=df_merged1.index,
                    color=df_merged1['cases_per_100k'],
                    projection="mercator",
                    title="Daily Covid19 Cases Per 100,000 People in London Boroughs")

geo_cases.update_geos(fitbounds="locations", visible=False)

geo_cases.update_layout(plot_bgcolor = backgroundColor,
                  paper_bgcolor= backgroundColor,
                  geo=dict(bgcolor= 'rgba(0,0,0,0)'),
                  title = {'x':0.5}, 
                  font = {"family" : fontStyle, "color": textColor})

In [278]:
bar = px.bar(df, x=df['age_group'], y=df['Vaccination_Rate'], color="age_group", title='3rd Dose Vaccination Rate in London, By Among Age Group')
bar

In [279]:
young_population_pct = df_vaccinationYoung['population'].sum() 
adult_population_pct = df_vaccinationAdult['population'].sum() 
old_population_pct = df_vaccinationOld['population'].sum()

age_d = {'age_group': ['Young (12 - 17)', 'Adult (18 - 64)', 'Old (65+)'],
        'Population': [young_population_pct, adult_population_pct, old_population_pct]
        }
df_ageDemographic = pd.DataFrame(data=age_d)

ageDemographic = px.pie(df_ageDemographic, values='Population', names='age_group', title='Age Demographic in London')
ageDemographic

In [280]:
#font-style, color for the graphs.
fontStyle = 'courier'
backgroundColor = '#23262F'
textColor = 'white'

dailyCases.update_layout(plot_bgcolor = backgroundColor,
                  paper_bgcolor= backgroundColor,
                  title = {'x':0.5}, 
                  font = {"family" : fontStyle, "color": textColor})


bar.update_layout(plot_bgcolor = backgroundColor,
                  paper_bgcolor= backgroundColor,
                  title = {'x':0.5}, 
                  font = {"family" : fontStyle, "color": textColor})


#remove color in the graph background.
last14Days_graph.update_layout(plot_bgcolor = backgroundColor,
                  paper_bgcolor= backgroundColor,
                  title = {'x':0.5}, 
                  font = {"family" : fontStyle, "color": textColor})



ageDemographic.update_layout(plot_bgcolor = backgroundColor,
                  paper_bgcolor= backgroundColor,
                  title = {'x':0.5}, 
                  font = {"family" : fontStyle, "color": textColor})




#hide the gridlines.
last14Days_graph.update_yaxes(showgrid=False)
dailyCases.update_yaxes(showgrid=False)
dailyCases.update_xaxes(showgrid=False)

In [281]:
app = dash.Dash(
    external_stylesheets=[dbc.themes.BOOTSTRAP, 'styles.css']
)

app.layout = dbc.Alert(
    "Hello, Bootstrap!", className="m-5"
)

    


app.layout = dbc.Container([
    dbc.Row([
            dbc.Row([
            html.Div(children=[html.H1(id='Title', children='London Covid-19 Tracker'),   
                              html.Div(id='subheading', style={}, children='''
                              Tracking the impact of covid on london healthcare
                            ''') ])


            ]),

            dbc.Row([
                html.Label(id='date', children='Last Updated: ' + currentDate)
            ]),

            dbc.Row([
                dbc.Col([
                    html.Br(),
                    html.Label('Region'),
                    dcc.Dropdown(id = 'drop-down', 
                                 options = df_cases['area_name'].unique(),
    #                              value = df['area_name'].iloc[0],
                                 )
                ]),
                dbc.Col([
                    html.Br(),
                    html.Label('Metric'),
                    dcc.Dropdown(options = ['Covid-19 Daily Data'],
                                value = 'Covid-19 Daily Data')
                ]),
            ])

        ]),
    
    html.Div(
        id='info-section',
        children=dbc.Row([
                dbc.Col([
                    dbc.Row([
                        dbc.Row([
                            html.Div(
                                className='stat-box',
                                children=[
                                    html.Label(className='info-header', children='Total Case'),
                                    html.Div(className='stat', id='total-cases', children=total_cases)                                   
                                ]
                            )
                        ]),
                        dbc.Row([
                            html.Div(
                                className='stat-box',
                                children=[
                                    html.Label(className='info-header', children='Total Death'),
                                    html.Div(className='stat', id='total-deaths', children=total_deaths)
                                ]
                            )                        
                        ]),
                        dbc.Row([
                            html.Div(
                                className='stat-box',
                                children=[
                                    html.Label(className='info-header', children='New Cases'),
                                    html.Div(className='stat', id='new-cases', children=new_cases),
                                    html.Div(className="info-change", style={}, children='''Change in Daily Case: '''+ str(new_cases - new_cases_previous))
                                ]
                            )
                        ]),
                        dbc.Row([
                            html.Div(
                                className='stat-box',
                                children=[                    
                                    html.Label(className='info-header', children='New Deaths'),
                                    html.Div(className='stat', id='new-deaths', children=new_deaths),
                                    html.Div(className="info-change", style={}, children='''Change in Daily Death: '''+ str(new_deaths - new_deaths_previous)),
                                ]
                            )
                        ]),
                        dbc.Row([
                            html.Div(
                                className='stat-box',
                                children=[  
                                    html.Label(className='info-header', children='Third Dose Vaccination Rate'),
                                    html.Div(className='stat', id='vax-rate', children=str(vax_rate) + '%')
                                ]
                            )
                        ])                              
                    ]),
                    dbc.Row([
                        dcc.Graph(className='graph', id = 'age-demographic', figure=ageDemographic),
                        dcc.Graph(className='graph', id = 'vax-age-group', figure=bar),
                    ])

                ]),
                dbc.Col([
                    dcc.Graph(className='graph', id = 'indicator-graph', figure=dailyCases),
                    dcc.Graph(className='graph', id='2week-graph', figure=last14Days_graph),
                    dcc.Graph(figure=geo_cases)
                ]),      

            ])
    )
    

    
    
])

#update interface.
@app.callback([Output('indicator-graph', 'figure'),
              Output('2week-graph', 'figure'),
              Output('total-cases', 'children'),
              Output('new-cases', 'children'),
               Output('total-deaths', 'children'),
               Output('new-deaths', 'children'),
              Output('vax-rate', 'children'),
              Output('vax-age-group', 'figure'),
              Output('age-demographic', 'figure')],
              Input('drop-down', 'value'))
def update_output(value):
    #shows line chart of past covid cases.
    df1 = df_merged.loc[df_merged['area_name'] == value]
    x = df1['date']
    y = df1['cases_per_100k']

    last14Days = df1.tail(14)
    last14Days_graph = px.bar(last14Days, x=last14Days['date'], y=last14Days['new_cases'], title="Daily Cases Per 100,000 People in the Last 14 Days")
    
    total_cases = df1['new_cases'].sum()
    new_cases = df1['new_cases'].iloc[-1]
    
    total_deaths = df1['new_deaths'].sum()
    new_deaths = df1['new_deaths'].iloc[-1]
    

    #update info on vaccination, by boroughs.
    df2 = df_3rdDose.copy().loc[df_3rdDose['area_name'] == value]
    vax_rate = round((df2['cum_doses'].sum() / df2['population'].sum())*100)
    
    
    df_vaccinationYoung = df2.loc[df2['age_lower'] < 18]
    df_vaccinationAdult = df2.loc[df2['age_lower'] < 65]
    df_vaccinationOld = df2.loc[df2['age_lower'] >= 65]
    
    
    df_vaccinationYoung_pct = df_vaccinationYoung['cum_doses'].sum() / df_vaccinationYoung['population'].sum()
    df_vaccinationAdult_pct = df_vaccinationAdult['cum_doses'].sum() / df_vaccinationAdult['population'].sum()
    df_vaccinationOld_pct = df_vaccinationOld['cum_doses'].sum() / df_vaccinationOld['population'].sum()
    
    
    d = {'age_group': ['Young (12 - 17)', 'Adult (18 - 64)', 'Old (65+)'],
        'Vaccination_Rate': [df_vaccinationYoung_pct, df_vaccinationAdult_pct, df_vaccinationOld_pct]
        }
    df = pd.DataFrame(data=d)
    
    bar = px.bar(df, x=df['age_group'],
                 color="age_group",
                 y=df['Vaccination_Rate'],
                 title='3rd Dose Vaccination Rate in ' + value + ', By Age Group')
    
    
    
    young_population_pct = df_vaccinationYoung['population'].sum()
    adult_population_pct = df_vaccinationAdult['population'].sum()
    old_population_pct = df_vaccinationOld['population'].sum()

    age_d = {'age_group': ['Young (12 - 17)', 'Adult (18 - 64)', 'Old (65+)'],
            'Population': [young_population_pct, adult_population_pct, old_population_pct]
            }
    df_ageDemographic = pd.DataFrame(data=age_d)

    ageDemographic = px.pie(df_ageDemographic, values='Population', names='age_group', title='Age Demographic in ' + value)
    
  
    
    
    
    dailyCases = px.line(df1, x=x, y=y, title="Daily Covid19 Cases Per 100,000 People in " + value)
     
    #font-style, color for the graphs.
    fontStyle = 'courier'
    backgroundColor = '#23262F'
    textColor = 'white'

    dailyCases.update_layout(plot_bgcolor = backgroundColor,
                      paper_bgcolor= backgroundColor,
                      title = {'x':0.5}, 
                      font = {"family" : fontStyle, "color": textColor})
    
    bar.update_layout(plot_bgcolor = backgroundColor,
                      paper_bgcolor= backgroundColor,
                      title = {'x':0.5}, 
                      font = {"family" : fontStyle, "color": textColor})


    #remove color in the graph background.
    last14Days_graph.update_layout(plot_bgcolor = backgroundColor,
                      paper_bgcolor= backgroundColor,
                      title = {'x':0.5}, 
                      font = {"family" : fontStyle, "color": textColor})



    ageDemographic.update_layout(plot_bgcolor = backgroundColor,
                      paper_bgcolor= backgroundColor,
                      title = {'x':0.5}, 
                      font = {"family" : fontStyle, "color": textColor})
    
    
     


    #hide the gridlines.
    last14Days_graph.update_yaxes(showgrid=False)
    dailyCases.update_yaxes(showgrid=False)
    dailyCases.update_xaxes(showgrid=False)
    
    
    
    
    
    return dailyCases, last14Days_graph, total_cases, new_cases,  total_deaths, new_deaths, str(vax_rate) + '%', bar, ageDemographic



if __name__ == '__main__':
    app.run_server(debug=True, use_reloader=False)

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is run